# Assignment 3

By : Sonu Adhikari


# Importing necessary libraries

In [302]:
import numpy as np
import pandas as pd
from io import StringIO

In [303]:
import torch, torchdata, torchtext
from torch import nn
import torch.nn.functional as F

import random, math, time

device = torch.device('cuda:2' if torch.cuda.is_available() else 'cpu')
print(device)

#make our work comparable if restarted the kernel
SEED = 1234
torch.manual_seed(SEED)
torch.backends.cudnn.deterministic = True

cpu


In [304]:
torch.__version__

'2.2.0+cpu'

In [305]:
torchtext.__version__

'0.16.2+cpu'

## 1. ETL: Loading the dataset

Here I have chosen to translate between Nepali and English Language. Dataset was sourced from a github page.This is a collection of news articles in Nepali that has been translated. It was a gzip compressed text file. The size was too big so I reduced the file size so that the training time would be reduced. I reduced the dataset from 100k sentences with english to nepali translation to 10k(approx.) for smoother training. But the kernel kept crash after several hours. I am still working on it. Will update the github later on.

In [306]:
# Open the text file in read mode
with open('en-nep-10k.txt', 'r', encoding='utf-8') as f:
    # Read the entire contents of the file into a string
    file_content = f.read()

# Print the contents of the file
print(file_content)

York is a collegiate university and every student is allocated to one of the university’s nine colleges. The ninth college was founded in 2014 and was named Constantine after the Roman emperor Constantine the Great, who was proclaimed Augustus in York in 306 AD.	न्यूयोर्क एक collegiate विश्वविद्यालय छ र हरेक विद्यार्थी विश्वविद्यालय गरेको नौ कलेज को एक विनियोजन गरिएको छ. नवौं कलेज मा स्थापित भएको थियो 2014 र रोमन सम्राट Constantine महान् पछि नाम थियो Constantine, जो मा योर्क अगस्तस घोषणा भएको थियो 306 ई. त्यहाँ निकट भविष्यमा दशौं कलेज निर्माण गर्ने योजना हो.
40:8 All my enemies were whispering against me . They were thinking up evils against me .	40:8 मेरो सबै शत्रुलाई मेरो विरुद्धमा कानेखुसी थिए. तिनीहरू मेरो विरूद्धमा अप दुष्कर्मलाई सोच थियो.
During the Presidency of Edmund J . James (1904-1920), James is credited for building the foundation of the large Chinese international student population on campus . James established ties with China through the Chinese Minister to the United S

In [307]:
file_content = file_content.replace("\r", "")

In [308]:
df = pd.read_csv(StringIO(file_content),sep='\t|\n',header=None)

C:\Users\Dell\AppData\Local\Temp\ipykernel_3096\3256766710.py:1: ParserWarning: Falling back to the 'python' engine because the 'c' engine does not support regex separators (separators > 1 char and different from '\s+' are interpreted as regex); you can avoid this warning by specifying engine='python'.
  df = pd.read_csv(StringIO(file_content),sep='\t|\n',header=None)


In [309]:
df.head()

0  \
0  York is a collegiate university and every stud...   
1  40:8 All my enemies were whispering against me...   
2  During the Presidency of Edmund J . James (190...   
3  These sequences are intercepted by the ANSI.SY...   
4  Do all my brothers, sisters, disillusioned, an...   

                                                   1  
0  न्यूयोर्क एक collegiate विश्वविद्यालय छ र हरेक...  
1  40:8 मेरो सबै शत्रुलाई मेरो विरुद्धमा कानेखुसी...  
2  पुस्तकालय, जसमा स्कूल संग खोलियो 1868, सुरु 1,...  
3  यी दृश्यहरु पीसी गरेको एक नम्बर मा CONFIG.SYS ...  
4  मेरा सबै भाइहरूलाई के, बहिनीहरू, रनभुल्लमा, र ...

In [310]:
df.size

21682

In [311]:
df.shape

(10841, 2)

In [312]:
df2 = df.rename({0: 'eng', 1: 'nep'}, axis=1)

In [313]:
df2.head()

eng  \
0  York is a collegiate university and every stud...   
1  40:8 All my enemies were whispering against me...   
2  During the Presidency of Edmund J . James (190...   
3  These sequences are intercepted by the ANSI.SY...   
4  Do all my brothers, sisters, disillusioned, an...   

                                                 nep  
0  न्यूयोर्क एक collegiate विश्वविद्यालय छ र हरेक...  
1  40:8 मेरो सबै शत्रुलाई मेरो विरुद्धमा कानेखुसी...  
2  पुस्तकालय, जसमा स्कूल संग खोलियो 1868, सुरु 1,...  
3  यी दृश्यहरु पीसी गरेको एक नम्बर मा CONFIG.SYS ...  
4  मेरा सबै भाइहरूलाई के, बहिनीहरू, रनभुल्लमा, र ...

## 2. EDA - simple investigation

In [314]:
#let's take a look at one example of train
sample = next(iter(df2))
#sample

In [315]:
train_size = len(list(iter(sample)))
train_size

3

In [316]:
#splitting for smoother training process.
from sklearn.model_selection import train_test_split

train, test = train_test_split(df2, test_size=0.2,random_state=999)

In [317]:
len(train),len(test)

(8672, 2169)

In [318]:
train_data, val_data =  train_test_split(train, test_size=0.3,random_state=999)

In [319]:
len(train_data),len(val_data),len(test)

(6070, 2602, 2169)

In [320]:
train_data

eng  \
2377  Fully automatic Honey Filling Machine In Bottl...   
8296  Be friendly/supportive of others through a fai...   
8496  The bathing pleasure and ease of a modern hot ...   
4245  Participants interacted with each other and wi...   
194   2. Rhetoric, alaghah in Arabic, signifies use ...   
...                                                 ...   
1718  24 Blessed among women be Jahel the wife of Ha...   
259   The School of Pharmacy, University of London m...   
9068                                       Gulmi, Nepal   
3766  Author Topic: ASP.NET MVC Developer - Nimble I...   
1276                          Next article VSA v2 admin   

                                                    nep  
2377  बोतलहरूमा पूर्ण स्वचालित हनी भरिने मेशीन - शीर...  
8296  एक विफलता मार्फत अनुकूल / अरूको सहयोग हुन &amp...  
8496  आधुनिक गरम टब प्रयोग को स्नान खुशी र आसानी प्र...  
4245  तेस्रो दिन अर्थात अन्तिम दिनमा आदिवासी जनजातिल...  
194   2 Rhetoric, अरबी मा alaghah, भाषा को प्रयोग हो...  
...                                                 ...  
1718  24 याएल केनी हेबेरकी पत्नी थिइन्। तिनी सबै स्त...  
259   फार्मेसी को स्कूल, विश्वविद्यालय लन्डन को मा U...  
9068                                      गुल्मी, नेपाल  
3766  Author Topic: डिप्रेसन र एन्जाइटीको समस्या भोग...  
1276                                 अर्को लेखमा VSA v2  

[6070 rows x 2 columns]

## 3. Preprocessing 

### Tokenizing

First, since we have two languages, let's create some constants to represent that.  Also, let's create two dicts: one for holding our tokenizers and one for holding all the vocabs with assigned numbers for each unique word

I have used the following command in commented form to tokenize the Nepali language.

In [322]:
# nepali language tokenizer -> nepalitokenizer
# pip install nepalitokenizer

In [323]:
# Place-holders
token_transform = {}
vocab_transform = {}

In [324]:
from torchtext.data.utils import get_tokenizer
from nepalitokenizer import NepaliTokenizer

SRC_LANGUAGE= 'nep'
TRG_LANGUAGE= 'eng'

tokenize = NepaliTokenizer()

token_transform[SRC_LANGUAGE] = tokenize.tokenizer
token_transform[TRG_LANGUAGE] = get_tokenizer('spacy', language='en_core_web_sm')

In [325]:
# let's try tokenizing nepali language

tokenize = NepaliTokenizer()
print(tokenize.tokenizer('थाइल्यान्ड मा धेरै गर्मी छ नेपाल भन्दा'))

['थाइल्यान्ड', 'गर्मी', 'नेपाल']


In [326]:
token_transform[SRC_LANGUAGE]('थाइल्यान्ड मा धेरै गर्मी छ नेपाल भन्दा')

['थाइल्यान्ड', 'गर्मी', 'नेपाल']

In [327]:
#example of tokenization of the english part
print("Tokenization: ", token_transform[TRG_LANGUAGE]('Thailand is hotter than Nepal'))

Tokenization:  ['Thailand', 'is', 'hotter', 'than', 'Nepal']


A function to tokenize our input.

In [328]:
# helper function to yield list of tokens
def yield_tokens(data, language):
    language_index = {SRC_LANGUAGE: 0, TRG_LANGUAGE: 1}

    for data_sample in data:
        yield token_transform[language](data_sample[language_index[language]])

Before we tokenize, let's define some special symbols so our neural network understand the embeddings of these symbols, namely the unknown, the padding, the start of sentence, and end of sentence.

In [329]:
# Define special symbols and indices
UNK_IDX, PAD_IDX, SOS_IDX, EOS_IDX = 0, 1, 2, 3
# Make sure the tokens are in order of their indices to properly insert them in vocab
special_symbols = ['<unk>', '<pad>', '<sos>', '<eos>']

In [330]:
type(EOS_IDX)

int

### Text to integers (Numericalization)

Next we gonna create function (torchtext called vocabs) that turn these tokens into integers.  Here we use built in factory function <code>build_vocab_from_iterator</code> which accepts iterator that yield list or iterator of tokens.

In [331]:
yield_tokens(train_data, TRG_LANGUAGE)

<generator object yield_tokens at 0x00000152CD4FF970>

In [332]:
# build_vocab_from_iterator?

In [333]:
# making it iterable
# Note: The function build_vocab_from_iterator builds a vocab using a iterator only
# up until now, we have a dataframe so converting them to list
# makes it iterable

train_data = train_data.values.tolist()


In [334]:
from torchtext.vocab import build_vocab_from_iterator

for ln in [SRC_LANGUAGE, TRG_LANGUAGE]:
    # Create torchtext's Vocab object 
    vocab_transform[ln] = build_vocab_from_iterator(yield_tokens(train_data, ln), 
                                                    min_freq=2,   #if not, everything will be treated as UNK
                                                    specials=special_symbols,
                                                    special_first=True) #indicates whether to insert symbols at the beginning or at the end                                            
# Set UNK_IDX as the default index. This index is returned when the token is not found. 
# If not set, it throws RuntimeError when the queried token is not found in the Vocabulary. 
for ln in [SRC_LANGUAGE, TRG_LANGUAGE]:
    vocab_transform[ln].set_default_index(UNK_IDX)

In [335]:
#see some example
vocab_transform[TRG_LANGUAGE](['here', 'is', 'a', 'unknownword', 'a'])

[0, 928, 1514, 0, 1514]

In [336]:
vocab_transform[TRG_LANGUAGE](['बिरामी', 'अभ्यास', 'प्राधिकरणको','संग'])

[1820, 727, 6368, 28]

In [337]:
#we can reverse it....
mapping = vocab_transform[TRG_LANGUAGE].get_itos()

#print 1816, for example
mapping[11150]

'हुनेछन'

In [338]:
#we can reverse it....
mapping = vocab_transform[SRC_LANGUAGE].get_itos()

#print 1816, for example
mapping[4]

'the'

In [339]:
#let's try unknown vocab
mapping[0]
#they will all map to <unk> which has 0 as integer

'<unk>'

In [340]:
#let's try special symbols
mapping[1], mapping[2], mapping[3]

('<pad>', '<sos>', '<eos>')

In [341]:
#check unique vocabularies
len(mapping)

12609

## 4. Preparing the dataloader

One thing we change here is the <code>collate_fn</code> which now also returns the length of sentence.  This is required for <code>packed_padded_sequence</code>

In [342]:
from torch.nn.utils.rnn import pad_sequence
from torch.utils.data import DataLoader

BATCH_SIZE = 8

# helper function to club together sequential operations
def sequential_transforms(*transforms):
    def func(txt_input):
        for transform in transforms:
            txt_input = transform(txt_input)
        return txt_input
    return func

# function to add BOS/EOS and create tensor for input sequence indices
def tensor_transform(token_ids):
    return torch.cat((torch.tensor([SOS_IDX]), 
                      torch.tensor(token_ids), 
                      torch.tensor([EOS_IDX])))

# src and trg language text transforms to convert raw strings into tensors indices
text_transform = {}
for ln in [SRC_LANGUAGE, TRG_LANGUAGE]:
    text_transform[ln] = sequential_transforms(token_transform[ln], #Tokenization
                                               vocab_transform[ln], #Numericalization
                                               tensor_transform) # Add BOS/EOS and create tensor


# function to collate data samples into batch tesors
def collate_batch(batch):
    src_batch, src_len_batch, trg_batch = [], [], []
    for src_sample, trg_sample in batch:
        processed_text = text_transform[SRC_LANGUAGE](src_sample.rstrip("\n"))
        src_batch.append(processed_text)
        trg_batch.append(text_transform[TRG_LANGUAGE](trg_sample.rstrip("\n")))
        src_len_batch.append(processed_text.size(0))

    src_batch = pad_sequence(src_batch, padding_value=PAD_IDX)
    trg_batch = pad_sequence(trg_batch, padding_value=PAD_IDX)
    return src_batch, torch.tensor(src_len_batch, dtype=torch.int64), trg_batch

Create train, val, and test dataloaders

In [343]:
val_data = val_data.values.tolist()
test_data = test.values.tolist()

In [344]:
sample_train = next(iter(train_data))
sample_train

sample_val = next(iter(val_data))
sample_val

sample_test = next(iter(test_data))
sample_test

['Three Palestinians -- including a teenage girl -- and an Israeli soldier died on Monday in the latest violence.Palestinians blame changes to the status quo at the Al-Aqsa Mosque compound -- Islam\'s third most-holy site but known to Jews as Temple Mount -- as the spark for the bloodshed. Israel has repeatedly denied it is seeking to change the current rules, under which Jews and Christians can visit but only Muslims can pray at the site.- \'Concrete steps\' -Netanyahu has come under pressure to tighten security and on Monday he announced stricter controls on Palestinian vehicles and an increase in so-called "bypass roads," which create separate routes for Palestinians and Israeli settlers.',
 'इजरायल हवाई बलका अनुसार इजरायलतर्फबाट गरिएको यो हवाई आक्रमण प्यालेस्टाइनको रकेट आक्रमणको प्रतिक्रिया मात्र हो । तर हमास सुरक्षाबलका अनुसार इजरायलले गरेको हवाई आक्रमणमध्ये गाजा पट्टिमा अवस्थित ‘इस्लामिक मोभमेन्टस् मिलिटरी विङ्ग’को ‘एल बुरेजी रेफ्युजी क्याप’ लाई लक्ष्यगरी गरिएको थियो । यस आक्रमणब

In [345]:
sample_train=[]
sample_val=[]
sample_test= []
for x,y in enumerate(train_data):
    #x - index
    if x == 500:
        break
    sample_train.append(y)
    
for x,y in enumerate(val_data):
    #x - index
    if x == 450:
        break
    sample_val.append(y)


for x,y in enumerate(test_data):
    #x - index
    if x == 400:
        break
    sample_test.append(y)

In [346]:
batch_size = 2

sample_train_loader = DataLoader(sample_train, batch_size=batch_size,
                              shuffle=True, collate_fn=collate_batch)
sample_valid_loader = DataLoader(sample_val, batch_size=batch_size,
                              shuffle=True, collate_fn=collate_batch)
sample_test_loader  = DataLoader(sample_test, batch_size=batch_size,
                             shuffle=True, collate_fn=collate_batch)

In [347]:
batch_size = 8

train_loader = DataLoader(train_data, batch_size=batch_size,
                              shuffle=True, collate_fn=collate_batch)
valid_loader = DataLoader(val_data, batch_size=batch_size,
                              shuffle=True, collate_fn=collate_batch)
test_loader  = DataLoader(test_data, batch_size=batch_size,
                             shuffle=True, collate_fn=collate_batch)

Let's test the train loader.

In [348]:
for nep, _, eng in train_loader:
    break

In [349]:
print("Nepali shape: ", nep.shape)  # (seq len, batch_size)
print("English shape: ", eng.shape)   # (seq len, batch_size)

Nepali shape:  torch.Size([58, 8])
English shape:  torch.Size([91, 8])


## 5. Design the model

### Encoder

The changes here all within the `forward` method. It now accepts the lengths of the source sentences as well as the sentences themselves. 

After the source sentence (padded automatically within the iterator) has been embedded, we can then use `pack_padded_sequence` on it with the lengths of the sentences. Note that the tensor containing the lengths of the sequences must be a CPU tensor as of the latest version of PyTorch, which we explicitly do so with `to('cpu')`. `packed_embedded` will then be our packed padded sequence. This can be then fed to our RNN as normal which will return `packed_outputs`, a packed tensor containing all of the hidden states from the sequence, and `hidden` which is simply the final hidden state from our sequence. `hidden` is a standard tensor and not packed in any way, the only difference is that as the input was a packed sequence, this tensor is from the final **non-padded element** in the sequence.

We then unpack our `packed_outputs` using `pad_packed_sequence` which returns the `outputs` and the lengths of each, which we don't need. 

The first dimension of `outputs` is the padded sequence lengths however due to using a packed padded sequence the values of tensors when a padding token was the input will be all zeros.

In [350]:
class Encoder(nn.Module):
    def __init__(self, input_dim, emb_dim, hid_dim, dropout):
        super().__init__()
        
        self.embedding = nn.Embedding(input_dim, emb_dim)
        self.rnn = nn.GRU(emb_dim, hid_dim, bidirectional = True)
        self.fc = nn.Linear(hid_dim * 2, hid_dim)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, src, src_len):
        
        #src = [src len, batch size]
        #src_len = [batch size]
        
        embedded = self.dropout(self.embedding(src))
        #embedded = [src len, batch size, emb dim]
                
        #need to explicitly put lengths on cpu!
        packed_embedded = nn.utils.rnn.pack_padded_sequence(embedded, src_len.to('cpu'), enforce_sorted=False)
                
        packed_outputs, hidden = self.rnn(packed_embedded)        
        #packed_outputs is a packed sequence containing all hidden states
        #hidden is now from the final non-padded element in the batch
            
        outputs, _ = nn.utils.rnn.pad_packed_sequence(packed_outputs) 
        #outputs is now a non-packed sequence, all hidden states obtained
        #  when the input is a pad token are all zeros
            
        #outputs = [src len, batch size, hid dim * num directions]
        #hidden = [n layers * num directions, batch size, hid dim]
        
        #hidden is stacked [forward_1, backward_1, forward_2, backward_2, ...]
        #outputs are always from the last layer
        
        #hidden [-2, :, : ] is the last of the forwards RNN 
        #hidden [-1, :, : ] is the last of the backwards RNN
        
        #initial decoder hidden is final hidden state of the forwards and backwards 
        #  encoder RNNs fed through a linear layer
        hidden = torch.tanh(self.fc(torch.cat((hidden[-2,:,:], hidden[-1,:,:]), dim = 1)))
        
        #outputs = [src len, batch size, hid dim * 2]
        #hidden = [batch size, hid dim]
        
        return outputs, hidden

### Attention

I have tried to use all three Attention types from this point onwards.

In [351]:
class Attention(nn.Module):
    def __init__(self, hid_dim, variants):
        super().__init__()
        self.variants = variants
        self.v = nn.Linear(hid_dim, 1, bias = False)
        self.W = nn.Linear(hid_dim,     hid_dim) #for decoder
        self.U = nn.Linear(hid_dim * 2, hid_dim) #for encoder outputs
                
    def forward(self, hidden, encoder_outputs, mask):
        
        #hidden = [batch size, hid dim]
        #encoder_outputs = [src len, batch size, hid dim * 2]
        
        batch_size = encoder_outputs.shape[1]
        src_len = encoder_outputs.shape[0]

        encoder_outputs = encoder_outputs.permute(1, 0, 2)
        #encoder_outputs = [batch size, src len, hid dim * 2]

        if self.variants == 'additive': #additive attention
            #repeat decoder hidden state src_len times
            hidden = hidden.unsqueeze(1).repeat(1, src_len, 1)
            #hidden = [batch size, src len, hid dim]
            
            energy = torch.tanh(self.W(hidden) + self.U(encoder_outputs))
            #energy = [batch size, src len, hid dim]
            
            attention = self.v(energy).squeeze(2)
            #attention = [batch size, src len]

            #use masked_fill_ if you want in-place
            attention = attention.masked_fill(mask, -1e10)
            
        elif self.variants == 'general': #general attention
            hidden = hidden.unsqueeze(1).repeat(1, 1, 2)
            #hidden = [batch size, 1, hid dim*2]
            #encoder_outputs = [batch size, hid dim * 2, src len]

            energy = torch.bmm(hidden, encoder_outputs.transpose(1, 2))
            attention = energy.squeeze(1)
            #attention = [batch size, src len]

        elif self.variants == 'multiplicative': #multiplicative attention
            wh = self.W(hidden).unsqueeze(1).repeat(1, 1, 2)
            #wh = [batch size, 1, hid dim*2]
            #encoder_outputs = [batch size, hid dim * 2, src len]

            energy = torch.bmm(wh, encoder_outputs.transpose(1, 2))
            attention = energy.squeeze(1)

        #attention = [batch size, src len]
        return F.softmax(attention, dim = 1)

Let's see how the masked_fill work, just so you have faith

In [352]:
#example of masked_fill
#reall that 1 is pad_idx
x = torch.tensor([ [9, 1, 7, 2, 1, 1], [99, 1, 1, 0, 8, 9] ])

mask = (x == PAD_IDX)

x.masked_fill_(mask, -1e10)
print(x)

tensor([[           9, -10000000000,            7,            2, -10000000000,
         -10000000000],
        [          99, -10000000000, -10000000000,            0,            8,
                    9]])


### Decoder

The decoder only needs a few small changes. It needs to accept a mask over the source sentence and pass this to the attention module. As we want to view the values of attention during inference, we also return the attention tensor.

In [353]:
class Decoder(nn.Module):
    def __init__(self, output_dim, emb_dim, hid_dim, dropout, attention):
        super().__init__()

        self.output_dim = output_dim
        self.attention = attention
        self.embedding = nn.Embedding(output_dim, emb_dim)
        self.rnn = nn.GRU((hid_dim * 2) + emb_dim, hid_dim)
        self.fc_out = nn.Linear((hid_dim * 2) + hid_dim + emb_dim, output_dim)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, input, hidden, encoder_outputs, mask):
             
        # input = [batch size]
        # hidden = [batch size, hid dim]
        # encoder_outputs = [src len, batch size, hid dim * 2]
        # mask = [batch size, src len]
        
        input = input.unsqueeze(0)
        # input = [1, batch size]
        
        embedded = self.dropout(self.embedding(input))
        # embedded = [1, batch size, emb dim]
        
        a = self.attention(hidden, encoder_outputs, mask)
        # a = [batch size, src len]
        
        a = a.unsqueeze(1)
        # a = [batch size, 1, src len]
        
        weighted = torch.bmm(a, encoder_outputs.permute(1, 0, 2))
        # weighted = [batch size, 1, hid dim * 2]
        
        weighted = weighted.permute(1, 0, 2)
        # weighted = [1, batch size, hid dim * 2]
        
        rnn_input = torch.cat((embedded, weighted), dim=2)
        # rnn_input = [1, batch size, (hid dim * 2) + emb dim]
            
        output, hidden = self.rnn(rnn_input, hidden.unsqueeze(0))
        # output = [seq len, batch size, dec hid dim * n directions]
        # hidden = [n layers * n directions, batch size, hid dim]
        
        assert (output == hidden).all()
        
        embedded = embedded.squeeze(0)
        output = output.squeeze(0)
        weighted = weighted.squeeze(0)
        
        prediction = self.fc_out(torch.cat((output, weighted, embedded), dim=1))
        # prediction = [batch size, output dim]
        
        return prediction, hidden.squeeze(0), a.squeeze(1)


### Putting them together (become Seq2Seq!)

The overarching seq2seq model also needs a few changes for packed padded sequences, masking and inference. 

We need to tell it what the indexes are for the pad token and also pass the source sentence lengths as input to the `forward` method.

We use the pad token index to create the masks, by creating a mask tensor that is 1 wherever the source sentence is not equal to the pad token. This is all done within the `create_mask` function.

The sequence lengths as needed to pass to the encoder to use packed padded sequences.

The attention at each time-step is stored in the `attentions` 

In [354]:
class Seq2SeqPackedAttention(nn.Module):
    def __init__(self, encoder, decoder, src_pad_idx, device):
        super().__init__()
        
        self.encoder = encoder
        self.decoder = decoder
        self.src_pad_idx = src_pad_idx
        self.device = device
        
    def create_mask(self, src):
        #src: [src len, batch size]
        
        mask = (src == self.src_pad_idx).permute(1, 0)
        #mask: [batch size, src len]
        #we need to permute to make the mask same shape as attention...
        return mask

        
    def forward(self, src, src_len, trg, teacher_forcing_ratio = 0.5):
        
        #src: [src len, batch size]
        #src len: [batch size]
        #trg: [trg len, batch size]
        
        batch_size = src.shape[1]
        trg_len    = trg.shape[0]
        trg_vocab_size = self.decoder.output_dim #define in decoder
        
        #because decoder decodes each step....let's create a list that gonna append the result to this guy
        outputs = torch.zeros(trg_len, batch_size, trg_vocab_size).to(self.device)
        
        #because decoder decodes each step....let's memorize the attention done in each step....
        attentions = torch.zeros(trg_len, batch_size, src.shape[0]).to(self.device)
        
        #let's start!!!
        #1. encoder
        encoder_outputs, hidden = self.encoder(src, src_len)
        #encoder_outputs: [src len, batch size, hid dim * num directions]
        #hidden: [batch size, hid dim]
        
        #set the first input to the decoder
        input_ = trg[0,:]  #basically <sos>
        
        #create the mask for use in this step
        mask = self.create_mask(src)
        
        #2. for each of trg word
        for t in range(1, trg_len):

            #3. decode (hidden is always carry forward)
            output, hidden, attention = self.decoder(input_, hidden, encoder_outputs, mask)
            #output:   [batch size, output_dim]
            #hidden:   [batch size, hid_dim]
            #attention::[batch size, src len]  ==> how each of src token is important to input_ 
            
            #4. append the results to outputs and attentions
            outputs[t] = output
            attentions[t] = attention
            
            #5. get the result, using argmax
            top1 = output.argmax(1)  #find the maximum index of dimension 1, which is output_dim
            
            #6. based on the teacher forcing ratio, 
            teacher_force_or_not = random.random() < teacher_forcing_ratio
                    #if teacher forcing, next input is the next trg
                    #if no teacher forcing, the next input is the argmax guy...
            input_ = trg[t] if teacher_force_or_not else top1  #autoregressive
            
        return outputs, attentions #outputs for predicting the word, attentions to see which word is important
        
        

## 6. Training

We use a simplified version of the weight initialization scheme used in the paper. Here, we will initialize all biases to zero and all weights from $\mathcal{N}(0, 0.01)$.

In [355]:
def initialize_weights(m):
    for name, param in m.named_parameters():
        if 'weight' in name:
            nn.init.normal_(param.data, mean=0, std=0.01)
        else:
            nn.init.constant_(param.data, 0)

In [356]:
device

device(type='cpu')

In [357]:
type(initialize_weights)

function

## General Attention

In [358]:
input_dim = len(vocab_transform[SRC_LANGUAGE])
output_dim = len(vocab_transform[TRG_LANGUAGE])
emb_dim = 256  
hid_dim = 512  
dropout = 0.5
SRC_PAD_IDX = PAD_IDX


attn = Attention(hid_dim, variants='general')
enc = Encoder(input_dim, emb_dim, hid_dim, dropout)
dec = Decoder(output_dim, emb_dim, hid_dim, dropout, attn)

model_general = Seq2SeqPackedAttention(enc, dec, SRC_PAD_IDX, device).to(device)
model_general.apply(initialize_weights)


Seq2SeqPackedAttention(
  (encoder): Encoder(
    (embedding): Embedding(12609, 256)
    (rnn): GRU(256, 512, bidirectional=True)
    (fc): Linear(in_features=1024, out_features=512, bias=True)
    (dropout): Dropout(p=0.5, inplace=False)
  )
  (decoder): Decoder(
    (attention): Attention(
      (v): Linear(in_features=512, out_features=1, bias=False)
      (W): Linear(in_features=512, out_features=512, bias=True)
      (U): Linear(in_features=1024, out_features=512, bias=True)
    )
    (embedding): Embedding(11220, 256)
    (rnn): GRU(1280, 512)
    (fc_out): Linear(in_features=1792, out_features=11220, bias=True)
    (dropout): Dropout(p=0.5, inplace=False)
  )
)

In [359]:
#we can print the complexity by the number of parameters
def count_parameters(model):
    params = [p.numel() for p in model.parameters() if p.requires_grad]
    for item in params:
        print(f'{item:>6}')
    print(f'______\n{sum(params):>6}')
    
count_parameters(model_general)

3227904
393216
786432
  1536
  1536
393216
786432
  1536
  1536
524288
   512
   512
262144
   512
524288
   512
2872320
1966080
786432
  1536
  1536
20106240
 11220
______
32651476


Our loss function calculates the average loss per token, however by passing the index of the `<pad>` token as the `ignore_index` argument we ignore the loss whenever the target token is a padding token. 

In [360]:
import torch.optim as optim

lr = 0.01

#training hyperparameters
optimizer = optim.Adam(model_general.parameters(), lr=lr)
criterion = nn.CrossEntropyLoss(ignore_index = PAD_IDX) #combine softmax with cross entropy

The training is very similar to part 1.

In [361]:
def train(model, loader, optimizer, criterion, clip, loader_length):
    
    model.train()
    epoch_loss = 0
    
    for src, src_length, trg in loader:
        
        
        #here?
        src = src.to(device)
        trg = trg.to(device)
        
        optimizer.zero_grad()
        
        output, attentions = model(src, src_length, trg)
        
        #trg    = [trg len, batch size]
        #output = [trg len, batch size, output dim]
        output_dim = output.shape[-1]
        
        #the loss function only works on 2d inputs with 1d targets thus we need to flatten each of them
        output = output[1:].view(-1, output_dim)
        trg    = trg[1:].view(-1)
        #trg    = [(trg len - 1) * batch size]
        #output = [(trg len - 1) * batch size, output dim]
        
        loss = criterion(output, trg)
        
        loss.backward()
        
        #clip the gradients to prevent them from exploding (a common issue in RNNs)
        torch.nn.utils.clip_grad_norm_(model.parameters(), clip)
        
        optimizer.step()
        
        epoch_loss += loss.item()
        
    return epoch_loss / loader_length

Our evaluation loop is similar to our training loop, however as we aren't updating any parameters we don't need to pass an optimizer or a clip value.

In [362]:
def evaluate(model, loader, criterion, loader_length):
        
    #turn off dropout (and batch norm if used)
    model.eval()
    
    epoch_loss = 0
    
    with torch.no_grad():
    
        for src, src_length, trg in loader:
        
            src = src.to(device)
            trg = trg.to(device)

            output, attentions = model(src, src_length, trg, 0) #turn off teacher forcing

            #trg    = [trg len, batch size]
            #output = [trg len, batch size, output dim]

            output_dim = output.shape[-1]
            
            output = output[1:].view(-1, output_dim)
            trg = trg[1:].view(-1)

            #trg    = [(trg len - 1) * batch size]
            #output = [(trg len - 1) * batch size, output dim]

            loss = criterion(output, trg)
            
            epoch_loss += loss.item()
        
    return epoch_loss / loader_length

### Putting everything together

In [363]:
train_loader_length = len(list(iter(train_loader)))
val_loader_length   = len(list(iter(valid_loader)))
test_loader_length  = len(list(iter(test_loader)))

In [364]:
sample_train_loader_length = len(list(iter(sample_train_loader)))
sample_val_loader_length   = len(list(iter(sample_valid_loader)))
sample_test_loader_length  = len(list(iter(sample_test_loader)))

In [365]:
type(sample_val_loader_length)

int

In [366]:
def epoch_time(start_time, end_time):
    elapsed_time = end_time - start_time
    elapsed_mins = int(elapsed_time / 60)
    elapsed_secs = int(elapsed_time - (elapsed_mins * 60))
    return elapsed_mins, elapsed_secs

 Note: The kernel kept on getting crashed after this point onward. As you can see. But I have attached the code base as much as I could.

In [ ]:
best_valid_loss = float('inf')
num_epochs = 1
clip = 1

save_path = f'models/{model_general.__class__.__name__}.pt'

train_losses = []
valid_losses = []

for epoch in range(num_epochs):
    
    start_time = time.time()
    
    print(start_time)
    print('Inside training now.....')
    train_loss = train(model_general, train_loader, optimizer, criterion, clip, train_loader_length)
    print('Inside evaluation now.....')
    valid_loss = evaluate(model_general, valid_loader, criterion, val_loader_length)
    
    # Train loss and validation loss calculation
    train_losses.append(train_loss)
    valid_losses.append(valid_loss)
    
    end_time = time.time()
    print(end_time)
    epoch_mins, epoch_secs = epoch_time(start_time, end_time)

    # Save the model if validation loss is decreased
    if valid_loss < best_valid_loss:
        best_valid_loss = valid_loss
        torch.save(model_general.state_dict(), save_path)
    
    print(f'Epoch: {epoch+1:02} | Time: {epoch_mins}m {epoch_secs}s')
    print(f'\tTrain Loss: {train_loss:.3f} | Train PPL: {math.exp(train_loss):7.3f}')
    print(f'\t Val. Loss: {valid_loss:.3f} |  Val. PPL: {math.exp(valid_loss):7.3f}')


1707400346.7474809
Inside training now.....


Inside evaluation now.....


: 

In [ ]:
import matplotlib.pyplot as plt
fig = plt.figure(figsize=(5, 3))
ax = fig.add_subplot(1, 1, 1)
ax.plot(train_losses, label = 'train loss')
ax.plot(valid_losses, label = 'valid loss')
plt.legend()
ax.set_xlabel('updates')
ax.set_ylabel('loss')

In [ ]:
model_general.load_state_dict(torch.load(save_path))
test_loss = evaluate(model_general, test_loader, criterion, test_loader_length)

print(f'| Test Loss: {test_loss:.3f} | Test PPL: {math.exp(test_loss):7.3f} |')

## Multiplicative Attention

In [ ]:
input_dim = len(vocab_transform[SRC_LANGUAGE])
output_dim = len(vocab_transform[TRG_LANGUAGE])
emb_dim = 256  
hid_dim = 512  
dropout = 0.5
SRC_PAD_IDX = PAD_IDX


attn = Attention(hid_dim, variants='multiplicative')
enc = Encoder(input_dim, emb_dim, hid_dim, dropout)
dec = Decoder(output_dim, emb_dim, hid_dim, dropout, attn)

model_multiplicative = Seq2SeqPackedAttention(enc, dec, SRC_PAD_IDX, device).to(device)
model_multiplicative.apply(initialize_weights)



In [ ]:
#we can print the complexity by the number of parameters
def count_parameters(model):
    params = [p.numel() for p in model.parameters() if p.requires_grad]
    for item in params:
        print(f'{item:>6}')
    print(f'______\n{sum(params):>6}')
    
count_parameters(model_multiplicative)

In [ ]:
import torch.optim as optim

PAD_IDX = 1

lr = 0.001

#training hyperparameters
optimizer = optim.Adam(model_multiplicative.parameters(), lr=lr)
criterion = nn.CrossEntropyLoss(ignore_index = PAD_IDX) #combine softmax with cross entropy

In [ ]:
best_valid_loss = float('inf')
num_epochs = 1
clip       = 1

save_path = f'models/{model_multiplicative.__class__.__name__}.pt'

train_losses = []
valid_losses = []

for epoch in range(num_epochs):
    
    start_time = time.time()

    train_loss = train(model_general, train_loader, optimizer, criterion, clip, train_loader_length)
    valid_loss = evaluate(model_general, valid_loader, criterion, val_loader_length)
    
    #for plotting
    train_losses.append(train_loss)
    valid_losses.append(valid_loss)
    
    end_time = time.time()
    
    epoch_mins, epoch_secs = epoch_time(start_time, end_time)

    
    if valid_loss < best_valid_loss:
        best_valid_loss = valid_loss
        torch.save(model_general.state_dict(), save_path)
    
    print(f'Epoch: {epoch+1:02} | Time: {epoch_mins}m {epoch_secs}s')
    print(f'\tTrain Loss: {train_loss:.3f} | Train PPL: {math.exp(train_loss):7.3f}')
    print(f'\t Val. Loss: {valid_loss:.3f} |  Val. PPL: {math.exp(valid_loss):7.3f}')
    
    #lower perplexity is better

In [ ]:
#For plotting
import matplotlib.pyplot as plt
fig = plt.figure(figsize=(5, 3))
ax = fig.add_subplot(1, 1, 1)
ax.plot(train_losses, label = 'train loss')
ax.plot(valid_losses, label = 'valid loss')
plt.legend()
ax.set_xlabel('updates')
ax.set_ylabel('loss')

In [ ]:

model_multiplicative.load_state_dict(torch.load(save_path))
test_loss = evaluate(model_multiplicative, test_loader, criterion, test_loader_length)

print(f'| Test Loss: {test_loss:.3f} | Test PPL: {math.exp(test_loss):7.3f} |')

## Additive Attention

In [ ]:
input_dim = len(vocab_transform[SRC_LANGUAGE])
output_dim = len(vocab_transform[TRG_LANGUAGE])
emb_dim = 256  
hid_dim = 512  
dropout = 0.5
SRC_PAD_IDX = PAD_IDX


attn = Attention(hid_dim, variants='additive')
enc = Encoder(input_dim, emb_dim, hid_dim, dropout)
dec = Decoder(output_dim, emb_dim, hid_dim, dropout, attn)

model_additive = Seq2SeqPackedAttention(enc, dec, SRC_PAD_IDX, device).to(device)
model_additive.apply(initialize_weights)



In [ ]:
#we can print the complexity by the number of parameters
def count_parameters(model):
    params = [p.numel() for p in model.parameters() if p.requires_grad]
    for item in params:
        print(f'{item:>6}')
    print(f'______\n{sum(params):>6}')
    
count_parameters(model_additive)

In [ ]:
import torch.optim as optim

lr = 0.001

#training hyperparameters
optimizer = optim.Adam(model_additive.parameters(), lr=lr)
criterion = nn.CrossEntropyLoss(ignore_index = PAD_IDX) #combine softmax with cross entropy

In [ ]:
best_valid_loss = float('inf')
num_epochs = 1
clip       = 1

save_path = f'models/{model_additive.__class__.__name__}.pt'

train_losses = []
valid_losses = []

for epoch in range(num_epochs):
    
    start_time = time.time()

    train_loss = train(model_general, train_loader, optimizer, criterion, clip, train_loader_length)
    valid_loss = evaluate(model_general, valid_loader, criterion, val_loader_length)
    
    #for plotting
    train_losses.append(train_loss)
    valid_losses.append(valid_loss)
    
    end_time = time.time()
    
    epoch_mins, epoch_secs = epoch_time(start_time, end_time)

    
    if valid_loss < best_valid_loss:
        best_valid_loss = valid_loss
        torch.save(model_general.state_dict(), save_path)
    
    print(f'Epoch: {epoch+1:02} | Time: {epoch_mins}m {epoch_secs}s')
    print(f'\tTrain Loss: {train_loss:.3f} | Train PPL: {math.exp(train_loss):7.3f}')
    print(f'\t Val. Loss: {valid_loss:.3f} |  Val. PPL: {math.exp(valid_loss):7.3f}')
    
    #lower perplexity is better

In [ ]:
import matplotlib.pyplot as plt
fig = plt.figure(figsize=(5, 3))
ax = fig.add_subplot(1, 1, 1)
ax.plot(train_losses, label = 'train loss')
ax.plot(valid_losses, label = 'valid loss')
plt.legend()
ax.set_xlabel('updates')
ax.set_ylabel('loss')

In [ ]:
model_additive.load_state_dict(torch.load(save_path))
test_loss = evaluate(model_additive, test_loader, criterion, test_loader_length)

print(f'| Test Loss: {test_loss:.3f} | Test PPL: {math.exp(test_loss):7.3f} |')

## 7. Test on some random news

In [ ]:
sample[0]

In [ ]:
sample[1]

In [ ]:
src_text = text_transform[SRC_LANGUAGE](sample[0]).to(device)
src_text

In [ ]:
trg_text = text_transform[TRG_LANGUAGE](sample[1]).to(device)
trg_text

In [ ]:
src_text = src_text.reshape(-1, 1)  #because batch_size is 1

In [ ]:
trg_text = trg_text.reshape(-1, 1)

In [ ]:
src_text.shape, trg_text.shape

In [ ]:
text_length = torch.tensor([src_text.size(0)]).to(dtype=torch.int64)

In [ ]:
model.load_state_dict(torch.load(save_path))

model.eval()
with torch.no_grad():
    output, attentions = model(src_text, text_length, trg_text, 0) #turn off teacher forcing

In [ ]:
output.shape #trg_len, batch_size, trg_output_dim

Since batch size is 1, we just take off that dimension

In [ ]:
output = output.squeeze(1)

In [ ]:
output.shape

We shall remove the first token since it's zeroes anyway

In [ ]:
output = output[1:]
output.shape #trg_len, trg_output_dim

Then we just take the top token with highest probabilities

In [ ]:
output_max = output.argmax(1) #returns max indices

In [ ]:
output_max

Get the mapping of the target language

In [ ]:
mapping = vocab_transform[TRG_LANGUAGE].get_itos()

In [ ]:
for token in output_max:
    print(mapping[token.item()])

## 8. Attention

Let's display the attentions to understand how the source text links with the generated text

In [ ]:
attentions.shape

In [ ]:
src_tokens = ['<sos>'] + token_transform[SRC_LANGUAGE](sample[0]) + ['<eos>']
src_tokens

In [ ]:
trg_tokens = ['<sos>'] + [mapping[token.item()] for token in output_max]
trg_tokens

In [ ]:
import matplotlib.ticker as ticker

def display_attention(sentence, translation, attention):
    
    fig = plt.figure(figsize=(10,10))
    ax = fig.add_subplot(111)
    
    attention = attention.squeeze(1).cpu().detach().numpy()
    
    cax = ax.matshow(attention, cmap='bone')
   
    ax.tick_params(labelsize=10)
    
    y_ticks =  [''] + translation
    x_ticks =  [''] + sentence 
     
    ax.set_xticklabels(x_ticks, rotation=45)
    ax.set_yticklabels(y_ticks)

    ax.xaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))

    plt.show()
    plt.close()

In [ ]:
display_attention(src_tokens, trg_tokens, attentions)

Note: Since I wasn;t able to load the notebook from the point the kernel crashed in general atention type, I am unable to show the training results comparison. However, I will update the results after resolving the issue asap.